In [1]:
import numpy
import datetime

#### Create a trajectory

Let's create a dummy trajectory

In [2]:
n_points = 100
lons = numpy.rad2deg([i * (numpy.pi/2) / n_points for i in range(n_points)])
lats = numpy.rad2deg([(i * numpy.pi/4) / n_points for i in range(n_points)])

Then we compute some parameters for each position of the trajectory

In [3]:
fieldA = [i**2 for i in range(n_points)]
fieldB = [i**3 for i in range(n_points)]

### Sending data to SEAScope

A granule has to belong to a collection, this is mandatory for SEAScope, so let's create a collection.

In [4]:
from SEAScope.lib.utils import create_collection

# Make sur to keep the collection identifier, we will need it later
collection_id, collection = create_collection('User - Trajectory')

Now that we have a collection and a trajectory, we can create the "shell" of the granule, ie. define where and when the granule will appear

In [5]:
from SEAScope.lib.utils import create_granule

start = datetime.datetime(2015, 12, 15)
stop = datetime.datetime(2015, 12, 30)

# Each position of the trajectory will be used as GCP
gcps = []
for i in range(0, len(lons)):
    gcp = {'lon': lons[i], 'lat': lats[i], 'i': i, 'j': 0}
    gcps.append(gcp)

granule_id, granule = create_granule(collection_id, gcps, start, stop)

The granule will contain each parameter as what we call a "field"

In [6]:
from SEAScope.lib.utils import set_field

set_field(granule, 'square', fieldA)
set_field(granule, 'cube', fieldB)

Now let's upload the collection and granule to SEAScope

In [7]:
import SEAScope.upload

# IP address and port used to reach the SEAScope standalone application
host = '127.0.0.1'
port = 11155

with SEAScope.upload.connect(host, port) as link:
    # Send create collection job
    SEAScope.upload.collection(link, collection)
    
    # Send create granule job
    SEAScope.upload.granule(link, granule)

1
1


### Telling SEAScope what to display

The next step is variables definition. A variable may be composed of
one or two fields (in which case they are considered to be horizontal and
vertical components of a vector).

In [8]:
from SEAScope.lib.utils import create_variable

# Create a variable for each parameter
var1 = create_variable(collection, 'aaa', ['square'], dims=1)
var2 = create_variable(collection, 'bbb', ['cube'], dims=1)

In [9]:
with SEAScope.upload.connect(host, port) as link:
    # Send create variable jobs
    SEAScope.upload.variable(link, var1)
    SEAScope.upload.variable(link, var2)

### Telling SEAScope how to display variables

In [10]:
rcfg1 = var1['rendering']
rcfg1['min'] = numpy.min(fieldA)
rcfg1['max'] = numpy.max(fieldA)
rcfg1['colormap'] = 'medspiration'

rcfg2 = var2['rendering']
rcfg2['min'] = numpy.min(fieldB)
rcfg2['max'] = numpy.max(fieldB)
rcfg2['colormap'] = 'pesket'

In [11]:
with SEAScope.upload.connect(host, port) as link:
    # Send create rendering config jobs
    SEAScope.upload.rendering_config(link, rcfg1)
    SEAScope.upload.rendering_config(link, rcfg2)

In [12]:
rcfg1['zindex'] = 0.1
with SEAScope.upload.connect(host, port) as link:
    # Send create rendering config jobs
    SEAScope.upload.rendering_config(link, rcfg1)